## Problem Statement

Can household characteristics predict who is having trouble with bills?

## Notes

1. Use NWEIGHT to get an actual population count for a given count of samples.
2. Only variables that had values of -8 and -9 were imputed.
3. -2 values are "not applicable" and were NOT imputed.

In [164]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import confusion_matrix, f1_score
import plotly.express as px

In [168]:
data = pd.read_csv('recs2015_public_v4.csv')

In [169]:
data.head()

DOEID  REGIONC  DIVISION METROMICRO UATYP10  TYPEHUQ  ZTYPEHUQ  CELLAR  \
0  10001        4        10      METRO       U        2         0       0   
1  10002        3         7       NONE       R        2         0       0   
2  10003        3         6      METRO       U        2         0       1   
3  10004        2         4      MICRO       C        2         0       1   
4  10005        1         2      METRO       U        2         0       1   

   ZCELLAR  BASEFIN    ...      ZELAMOUNT  NGXBTU  PERIODNG  ZNGAMOUNT  \
0        0       -2    ...              0  103.32         1          0   
1        0       -2    ...              1     NaN        -2         -2   
2        0        1    ...              0  100.14         1          0   
3        0        1    ...              0     NaN        -2         -2   
4        0        0    ...              0  102.83         1          0   

   FOXBTU  PERIODFO  ZFOAMOUNT  LPXBTU  PERIODLP  ZLPAMOUNT  
0  137.45        -2         -2   91.33        -2         -2  
1  137.45        -2         -2   91.33        -2         -2  
2  137.45        -2         -2   91.33        -2         -2  
3  137.45        -2         -2   91.33         2          0  
4  137.45        -2         -2   91.33        -2         -2  

[5 rows x 759 columns]

In [170]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5686 entries, 0 to 5685
Columns: 759 entries, DOEID to ZLPAMOUNT
dtypes: float64(262), int64(493), object(4)
memory usage: 32.9+ MB


## EDA

### Imputed variables

Imputed variables will have a corresponding z-flag (z version of the imputed column) indicated which values in that column were imputed.

In [171]:
# remove Z-columns
z_cols = data.columns[data.columns.str.startswith('Z')]
non_z_cols = data.columns[~data.columns.str.startswith('Z')]

In [172]:
z_cols

Index(['ZTYPEHUQ', 'ZCELLAR', 'ZBASEFIN', 'ZATTIC', 'ZATTICFIN', 'ZSTORIES',
       'ZPRKGPLC1', 'ZSIZEOFGARAGE', 'ZKOWNRENT', 'ZYEARMADERANGE',
       ...
       'ZHOTMA', 'ZWOODLOGS', 'ZWDPELLET', 'ZTOTSQFT_EN', 'ZWOODAMT',
       'ZPELLETAMT', 'ZELAMOUNT', 'ZNGAMOUNT', 'ZFOAMOUNT', 'ZLPAMOUNT'],
      dtype='object', length=217)

There are 217 z-columns (imputed)

In [173]:
(data[non_z_cols]==-2).sum().sum()

366178

There are a total of 366,178 `not applicable` values.

In [174]:
data_ = data[non_z_cols]

In [175]:
data_.shape

(5686, 542)

In [176]:
542*5686

3081812

There are a total of 3,081,812 response values.

In [177]:
366178/3081812

0.11881905839811124

This results in 11.9% of all responses being `not applicable`.

In [178]:
((data[non_z_cols]==-8) | (data[non_z_cols]==-9)).sum().sum()

13690

In [179]:
data.isnull().sum().sum()/3081812

0.0007729219043861209

There are a total of 13,690 (0.07%) responses that were "Refuse" or "Don't Know".

## Data Munging

### Rescaling Data Based on NWEIGHTS

Going to resample data based on the population each sample (row) represents. Each sample will be duplicated according to the scaling provided by the NWEIGHT column. First, divide NWEIGHT column by minimum NWEIGHT value and round to integer value. `weights_scaled` represents how many times each sample will be duplicated to resample the data properly.

In [181]:
def resample_data(data):
    # calculate the number of times to duplicate each sample
    weights_scaled = ((data['NWEIGHT']/data['NWEIGHT'].min())).astype(int)
    
    # duplicate the original indices based on weights_scaled
    resampled_idx = data_.index.repeat(weights_scaled.values)
    
    # create dummy dataframe with duplicated index and join original data
    resampled_data = pd.DataFrame(index=resampled_idx, columns=['dummy']).join(data)
    
    # delete dummy column and reset index
    resampled_data = resampled_data.drop('dummy', axis=1).reset_index(drop=True)
    
    return resampled_data

In [182]:
resampled_data = resample_data(data)

In [183]:
resampled_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92856 entries, 0 to 92855
Columns: 759 entries, DOEID to ZLPAMOUNT
dtypes: float64(262), int64(493), object(4)
memory usage: 537.7+ MB


The data cleaning steps taken are as follows:

1. Drop imputation flag columns (columns starting with z).
2. Set index to `DOEID`.
3. Drop replicate weight columns (columns starting with BRR).
4. Drop NWEIGHT which has already been used to scale the data.
5. Convert object (text) columns to dummy columns.

In [184]:
def clean_data(data):
    # get list of z and non-z columns
    z_cols = data.columns[data.columns.str.startswith('Z')]
    non_z_cols = data.columns[~data.columns.str.startswith('Z')]
    
    # remove z-columns
    resampled_data = data[non_z_cols]
    
    # set index
    resampled_data.set_index('DOEID', inplace=True)
    
    # drop unwanted columns
    cols_to_drop = [col for col in resampled_data.columns if 'BRR' in col]
    cols_to_drop.append('NWEIGHT') # sample weights
    cols_to_drop = cols_to_drop + ['ELXBTU','NGXBTU','FOXBTU','LPXBTU'] # btu conversion factors
    
    resampled_data = resampled_data.drop(cols_to_drop, axis=1)
    
    # get object datatype columns
    object_columns = []
    for col in resampled_data.columns:
        if resampled_data[col].dtype=='O':
            object_columns.append(col)
    # add object columns as dummies
    resampled_data = pd.concat([resampled_data, pd.get_dummies(resampled_data[object_columns])], axis=1)
    
    # drop the original object columns
    resampled_data = resampled_data.drop(object_columns, axis=1)
    
    return resampled_data

In [199]:
training_data = clean_data(resampled_data)
training_data.head()

REGIONC  DIVISION  TYPEHUQ  CELLAR  BASEFIN  ATTIC  ATTICFIN  STORIES  \
DOEID                                                                          
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   

       PRKGPLC1  SIZEOFGARAGE               ...                \
DOEID                                       ...                 
10001         1             2               ...                 
10001         1             2               ...                 
10001         1             2               ...                 
10001         1             2               ...                 
10001         1             2               ...                 

       IECC_CLIMATE_PUB_2B  IECC_CLIMATE_PUB_3A  IECC_CLIMATE_PUB_3B-4B  \
DOEID                                                                     
10001                    0                    0                       1   
10001                    0                    0                       1   
10001                    0                    0                       1   
10001                    0                    0                       1   
10001                    0                    0                       1   

       IECC_CLIMATE_PUB_3C  IECC_CLIMATE_PUB_4A  IECC_CLIMATE_PUB_4C  \
DOEID                                                                  
10001                    0                    0                    0   
10001                    0                    0                    0   
10001                    0                    0                    0   
10001                    0                    0                    0   
10001                    0                    0                    0   

       IECC_CLIMATE_PUB_5A  IECC_CLIMATE_PUB_5B-5C  IECC_CLIMATE_PUB_6A-6B  \
DOEID                                                                        
10001                    0                       0                       0   
10001                    0                       0                       0   
10001                    0                       0                       0   
10001                    0                       0                       0   
10001                    0                       0                       0   

       IECC_CLIMATE_PUB_7A-7B-7AK-8AK  
DOEID                                  
10001                               0  
10001                               0  
10001                               0  
10001                               0  
10001                               0  

[5 rows x 458 columns]

In [200]:
training_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 92856 entries, 10001 to 15686
Columns: 458 entries, REGIONC to IECC_CLIMATE_PUB_7A-7B-7AK-8AK
dtypes: float64(161), int64(275), uint8(22)
memory usage: 311.5 MB


#### Defining Hardship

In [201]:
def create_label(data, hardship_cols):
    
    # transform mapping
    xform = {0:0, 1:3, 2:2, 3:1}
    
    # remap the variables
    data['SCALEB'] = data['SCALEB'].map(xform)
    data['SCALEG'] = data['SCALEG'].map(xform)
    data['SCALEE'] = data['SCALEE'].map(xform)
    
    # create hardship label
    data['hardship_label'] = data['SCALEB'] + data['SCALEG'] + data['SCALEE']
    
    # drop the label columns from the dataset
    data = data.drop(['SCALEB', 'SCALEG', 'SCALEE'], axis=1)
    
    return data

In [202]:
hardship_cols = ['SCALEB', 'SCALEG', 'SCALEE']

# 'NOHEATBROKE', 'NOHEATEL', 'NOHEATNG', 'NOHEATBULK', 'COLDMA', 'HOTMA', 'NOACBROKE', 'NOACEL'

The hardship columns we've chosen are defined as follows:

`SCALEB`: Frequency of reducing or forgoing basic necessities due to home energy bill. <br>
`SCALEG`: Frequency of keeping home at unhealthy temperature. <br>
`SCALEE`: Frequency of receiving disconnect notice.

Let's look at the distributions of each of the 'hardship' columns.

In [203]:
fig = px.histogram(training_data, x="SCALEB", title='Histogram of SCALEB')
fig.update_layout(yaxis_title='Count', yaxis_type='log')
fig.show()

In [204]:
fig = px.histogram(training_data, x="SCALEG", title='Histogram of SCALEG')
fig.update_layout(yaxis_title='Count', yaxis_type='log')
fig.show()

In [205]:
fig = px.histogram(training_data, x="SCALEE", title='Histogram of SCALEE')
fig.update_layout(yaxis_title='Count', yaxis_type='log')
fig.show()

In [206]:
training_data.SCALEB.value_counts()

0    72893
2     8636
1     5879
3     5448
Name: SCALEB, dtype: int64

In [207]:
training_data.SCALEG.value_counts()

0    82791
2     4639
3     3938
1     1488
Name: SCALEG, dtype: int64

In [208]:
training_data.SCALEE.value_counts()

0    79306
3     7322
2     4400
1     1828
Name: SCALEE, dtype: int64

`SCALEB` has the most non-zero values while `SCALEG` has the least. We can see how the three `hardship` columns have different distributions.

In [209]:
# split the data into the training samples (X) and labels (y)
training_data = create_label(training_data, hardship_cols)
X = training_data.drop('hardship_label', axis=1)
y = training_data['hardship_label']
X.head()

REGIONC  DIVISION  TYPEHUQ  CELLAR  BASEFIN  ATTIC  ATTICFIN  STORIES  \
DOEID                                                                          
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   
10001        4        10        2       0       -2      0        -2       20   

       PRKGPLC1  SIZEOFGARAGE               ...                \
DOEID                                       ...                 
10001         1             2               ...                 
10001         1             2               ...                 
10001         1             2               ...                 
10001         1             2               ...                 
10001         1             2               ...                 

       IECC_CLIMATE_PUB_2B  IECC_CLIMATE_PUB_3A  IECC_CLIMATE_PUB_3B-4B  \
DOEID                                                                     
10001                    0                    0                       1   
10001                    0                    0                       1   
10001                    0                    0                       1   
10001                    0                    0                       1   
10001                    0                    0                       1   

       IECC_CLIMATE_PUB_3C  IECC_CLIMATE_PUB_4A  IECC_CLIMATE_PUB_4C  \
DOEID                                                                  
10001                    0                    0                    0   
10001                    0                    0                    0   
10001                    0                    0                    0   
10001                    0                    0                    0   
10001                    0                    0                    0   

       IECC_CLIMATE_PUB_5A  IECC_CLIMATE_PUB_5B-5C  IECC_CLIMATE_PUB_6A-6B  \
DOEID                                                                        
10001                    0                       0                       0   
10001                    0                       0                       0   
10001                    0                       0                       0   
10001                    0                       0                       0   
10001                    0                       0                       0   

       IECC_CLIMATE_PUB_7A-7B-7AK-8AK  
DOEID                                  
10001                               0  
10001                               0  
10001                               0  
10001                               0  
10001                               0  

[5 rows x 455 columns]

In [210]:
fig = px.histogram(training_data, x="hardship_label", title='Histogram of hardship_label')
fig.update_layout(yaxis_title='Count', yaxis_type='log')
fig.show()

The histogram above shows the distribution of hardship_label on a semilog plot. The vast majority of samples have a hardship_label of 0, indicating they had no hardship whatsoever.

## Train-Test Split

In [211]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, stratify=y, random_state=42)

In [212]:
y_train.value_counts()/len(y_train)

0    0.704274
1    0.074679
2    0.074229
3    0.053735
4    0.040040
5    0.023098
6    0.018871
7    0.005690
8    0.003874
9    0.001511
Name: hardship_label, dtype: float64

In [213]:
y_test.value_counts()/len(y_test)

0    0.704272
1    0.074666
2    0.074209
3    0.053715
4    0.040042
5    0.023105
6    0.018895
7    0.005711
8    0.003883
9    0.001501
Name: hardship_label, dtype: float64

Looking at the distributions above, we can verify that the original stratification of the data is maintained after the split.

## Model

In [214]:
# create RF classfier
rfc = RandomForestClassifier()

# train model
rfc.fit(X_train, y_train)

# compute predictions
predictions = rfc.predict(X_test)

In [215]:
confusion_matrix(y_test, predictions)

array([[21581,     0,     0,     0,     0,     0,     0,     0,     0,
            0],
       [    0,  2288,     0,     0,     0,     0,     0,     0,     0,
            0],
       [    0,     0,  2274,     0,     0,     0,     0,     0,     0,
            0],
       [    0,     0,     0,  1646,     0,     0,     0,     0,     0,
            0],
       [    0,     0,     0,     0,  1227,     0,     0,     0,     0,
            0],
       [    0,     0,     0,     0,     0,   708,     0,     0,     0,
            0],
       [    0,     0,     0,     0,     0,     0,   579,     0,     0,
            0],
       [    0,     0,     0,     0,     0,     0,     0,   175,     0,
            0],
       [    0,     0,     0,     0,     0,     0,     0,     0,   119,
            0],
       [    0,     0,     0,     0,     0,     0,     0,     0,     0,
           46]], dtype=int64)

The confusion matrix above indicates we had perfect predictions on all labels. This is likely because the `hardship` columns were computed based on other columns in the dataset. We should drop the 'SCALE' columns completely and compute our own hardship label based on the raw feature columns such as `NOHEATBROKE`.